In [1]:
# Import our dependencies
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler,OneHotEncoder
import pandas as pd
import tensorflow as tf

#  Import and read the charity_data.csv.
import pandas as pd 
application_df = pd.read_csv("charity_data.csv")
application_df.head()

EIN                                      NAME APPLICATION_TYPE  \
0  10520599              BLUE KNIGHTS MOTORCYCLE CLUB              T10   
1  10531628    AMERICAN CHESAPEAKE CLUB CHARITABLE TR               T3   
2  10547893        ST CLOUD PROFESSIONAL FIREFIGHTERS               T5   
3  10553066            SOUTHSIDE ATHLETIC ASSOCIATION               T3   
4  10556103  GENETIC RESEARCH INSTITUTE OF THE DESERT               T3   

        AFFILIATION CLASSIFICATION      USE_CASE  ORGANIZATION  STATUS  \
0       Independent          C1000    ProductDev   Association       1   
1       Independent          C2000  Preservation  Co-operative       1   
2  CompanySponsored          C3000    ProductDev   Association       1   
3  CompanySponsored          C2000  Preservation         Trust       1   
4       Independent          C1000     Heathcare         Trust       1   

      INCOME_AMT SPECIAL_CONSIDERATIONS  ASK_AMT  IS_SUCCESSFUL  
0              0                      N     5000              1  
1         1-9999                      N   108590              1  
2              0                      N     5000              0  
3    10000-24999                      N     6692              1  
4  100000-499999                      N   142590              1

In [2]:
#Deliverable 3, part 1: changing nn model
application_df = application_df.drop(columns=['EIN', 'NAME'])
application_df.head()

APPLICATION_TYPE       AFFILIATION CLASSIFICATION      USE_CASE  \
0              T10       Independent          C1000    ProductDev   
1               T3       Independent          C2000  Preservation   
2               T5  CompanySponsored          C3000    ProductDev   
3               T3  CompanySponsored          C2000  Preservation   
4               T3       Independent          C1000     Heathcare   

   ORGANIZATION  STATUS     INCOME_AMT SPECIAL_CONSIDERATIONS  ASK_AMT  \
0   Association       1              0                      N     5000   
1  Co-operative       1         1-9999                      N   108590   
2   Association       1              0                      N     5000   
3         Trust       1    10000-24999                      N     6692   
4         Trust       1  100000-499999                      N   142590   

   IS_SUCCESSFUL  
0              1  
1              1  
2              0  
3              1  
4              1

In [3]:
# Determine the number of unique values in each column.
application_cat = application_df.dtypes[application_df.dtypes == "object"].index.tolist()
application_df[application_cat].nunique()

APPLICATION_TYPE          17
AFFILIATION                6
CLASSIFICATION            71
USE_CASE                   5
ORGANIZATION               4
INCOME_AMT                 9
SPECIAL_CONSIDERATIONS     2
dtype: int64

In [4]:
# Look at APPLICATION_TYPE value counts for binning
app_type = application_df.APPLICATION_TYPE.value_counts()
app_type

T3     27037
T4      1542
T6      1216
T5      1173
T19     1065
T8       737
T7       725
T10      528
T9       156
T13       66
T12       27
T2        16
T25        3
T14        3
T29        2
T15        2
T17        1
Name: APPLICATION_TYPE, dtype: int64

In [5]:
# Determine which values to replace if counts are less than ...?
replace_application = list(app_type[app_type < 200].index)
    
# Replace in dataframe
for app in replace_application:
    application_df.APPLICATION_TYPE = application_df.APPLICATION_TYPE.replace(app,"Other")
    
# Check to make sure binning was successful
application_df.APPLICATION_TYPE.value_counts()

T3       27037
T4        1542
T6        1216
T5        1173
T19       1065
T8         737
T7         725
T10        528
Other      276
Name: APPLICATION_TYPE, dtype: int64

In [6]:
# Look at CLASSIFICATION value counts for binning
class_val = application_df.CLASSIFICATION.value_counts()
class_val.head()

C1000    17326
C2000     6074
C1200     4837
C3000     1918
C2100     1883
Name: CLASSIFICATION, dtype: int64

In [7]:
# Determine which values to replace if counts are less than ..?
replace_class = list(class_val[class_val < 300].index)

# Replace in dataframe
for cls in replace_class:
    application_df.CLASSIFICATION = application_df.CLASSIFICATION.replace(cls,"Other")
    
# Check to make sure binning was successful
application_df.CLASSIFICATION.value_counts()

C1000    17326
C2000     6074
C1200     4837
C3000     1918
C2100     1883
Other     1484
C7000      777
Name: CLASSIFICATION, dtype: int64

In [8]:
application_df[application_cat].nunique()

APPLICATION_TYPE          9
AFFILIATION               6
CLASSIFICATION            7
USE_CASE                  5
ORGANIZATION              4
INCOME_AMT                9
SPECIAL_CONSIDERATIONS    2
dtype: int64

In [9]:
# Create a OneHotEncoder instance
enc = OneHotEncoder(sparse=False)

# Fit and transform the OneHotEncoder using the categorical variable list
encode_df = pd.DataFrame(enc.fit_transform(application_df[application_cat]))

# Add the encoded variable names to the dataframe
encode_df.columns = enc.get_feature_names_out(application_cat)
encode_df.head()

APPLICATION_TYPE_Other  APPLICATION_TYPE_T10  APPLICATION_TYPE_T19  \
0                     0.0                   1.0                   0.0   
1                     0.0                   0.0                   0.0   
2                     0.0                   0.0                   0.0   
3                     0.0                   0.0                   0.0   
4                     0.0                   0.0                   0.0   

   APPLICATION_TYPE_T3  APPLICATION_TYPE_T4  APPLICATION_TYPE_T5  \
0                  0.0                  0.0                  0.0   
1                  1.0                  0.0                  0.0   
2                  0.0                  0.0                  1.0   
3                  1.0                  0.0                  0.0   
4                  1.0                  0.0                  0.0   

   APPLICATION_TYPE_T6  APPLICATION_TYPE_T7  APPLICATION_TYPE_T8  \
0                  0.0                  0.0                  0.0   
1                  0.0                  0.0                  0.0   
2                  0.0                  0.0                  0.0   
3                  0.0                  0.0                  0.0   
4                  0.0                  0.0                  0.0   

   AFFILIATION_CompanySponsored  ...  INCOME_AMT_1-9999  \
0                           0.0  ...                0.0   
1                           0.0  ...                1.0   
2                           1.0  ...                0.0   
3                           1.0  ...                0.0   
4                           0.0  ...                0.0   

   INCOME_AMT_10000-24999  INCOME_AMT_100000-499999  INCOME_AMT_10M-50M  \
0                     0.0                       0.0                 0.0   
1                     0.0                       0.0                 0.0   
2                     0.0                       0.0                 0.0   
3                     1.0                       0.0                 0.0   
4                     0.0                       1.0                 0.0   

   INCOME_AMT_1M-5M  INCOME_AMT_25000-99999  INCOME_AMT_50M+  \
0               0.0                     0.0              0.0   
1               0.0                     0.0              0.0   
2               0.0                     0.0              0.0   
3               0.0                     0.0              0.0   
4               0.0                     0.0              0.0   

   INCOME_AMT_5M-10M  SPECIAL_CONSIDERATIONS_N  SPECIAL_CONSIDERATIONS_Y  
0                0.0                       1.0                       0.0  
1                0.0                       1.0                       0.0  
2                0.0                       1.0                       0.0  
3                0.0                       1.0                       0.0  
4                0.0                       1.0                       0.0  

[5 rows x 42 columns]

In [10]:
# Merge one-hot encoded features and drop the originals
application_df = application_df.merge(encode_df,left_index=True, right_index=True)
application_df = application_df.drop(application_cat,1)
application_df.head()

C:\Users\ethan\anaconda3\envs\mlenv\lib\site-packages\ipykernel_launcher.py:3: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  This is separate from the ipykernel package so we can avoid doing imports until


STATUS  ASK_AMT  IS_SUCCESSFUL  APPLICATION_TYPE_Other  \
0       1     5000              1                     0.0   
1       1   108590              1                     0.0   
2       1     5000              0                     0.0   
3       1     6692              1                     0.0   
4       1   142590              1                     0.0   

   APPLICATION_TYPE_T10  APPLICATION_TYPE_T19  APPLICATION_TYPE_T3  \
0                   1.0                   0.0                  0.0   
1                   0.0                   0.0                  1.0   
2                   0.0                   0.0                  0.0   
3                   0.0                   0.0                  1.0   
4                   0.0                   0.0                  1.0   

   APPLICATION_TYPE_T4  APPLICATION_TYPE_T5  APPLICATION_TYPE_T6  ...  \
0                  0.0                  0.0                  0.0  ...   
1                  0.0                  0.0                  0.0  ...   
2                  0.0                  1.0                  0.0  ...   
3                  0.0                  0.0                  0.0  ...   
4                  0.0                  0.0                  0.0  ...   

   INCOME_AMT_1-9999  INCOME_AMT_10000-24999  INCOME_AMT_100000-499999  \
0                0.0                     0.0                       0.0   
1                1.0                     0.0                       0.0   
2                0.0                     0.0                       0.0   
3                0.0                     1.0                       0.0   
4                0.0                     0.0                       1.0   

   INCOME_AMT_10M-50M  INCOME_AMT_1M-5M  INCOME_AMT_25000-99999  \
0                 0.0               0.0                     0.0   
1                 0.0               0.0                     0.0   
2                 0.0               0.0                     0.0   
3                 0.0               0.0                     0.0   
4                 0.0               0.0                     0.0   

   INCOME_AMT_50M+  INCOME_AMT_5M-10M  SPECIAL_CONSIDERATIONS_N  \
0              0.0                0.0                       1.0   
1              0.0                0.0                       1.0   
2              0.0                0.0                       1.0   
3              0.0                0.0                       1.0   
4              0.0                0.0                       1.0   

   SPECIAL_CONSIDERATIONS_Y  
0                       0.0  
1                       0.0  
2                       0.0  
3                       0.0  
4                       0.0  

[5 rows x 45 columns]

In [11]:
# Split our preprocessed data into our features and target arrays
y = application_df.IS_SUCCESSFUL.values
X = application_df.drop(["IS_SUCCESSFUL"], 1).values

# Split the preprocessed data into a training and testing dataset
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=42, stratify=y)

C:\Users\ethan\anaconda3\envs\mlenv\lib\site-packages\ipykernel_launcher.py:3: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  This is separate from the ipykernel package so we can avoid doing imports until


In [12]:
# Create a StandardScaler instances
scaler = StandardScaler()

# Fit the StandardScaler
X_scaler = scaler.fit(X_train)

# Scale the data
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_test)

In [13]:
#OPTIMIZATION ATTEMPTS
#1: Dropped same two columns, layer 1 changed to 60 neurons, layer 2 changed to 25, epochs=100. Acc=72.
#2: Ran an optimizer, nothing did better than 72.8%
#3: Dropping less columns, binned names with only 1 loan request, top Acc= ~80%
#4: Based on #3, set up model with: Layer1=73, Layer 2=49, activation=tanh, epochs=200

In [14]:
# Define the model - deep neural net, i.e., the number of input features and hidden nodes for each layer.
number_input_features = len(X_train_scaled[0])
hidden_nodes_layer1 = 60
hidden_nodes_layer2 = 25

nn = tf.keras.models.Sequential()

# First hidden layer
nn.add(
    tf.keras.layers.Dense(units=hidden_nodes_layer1, input_dim=number_input_features, activation="relu")
)

# Second hidden layer
nn.add(tf.keras.layers.Dense(units=hidden_nodes_layer2, activation="relu"))

# Output layer
nn.add(tf.keras.layers.Dense(units=1, activation="sigmoid"))

# Check the structure of the model
nn.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense (Dense)               (None, 60)                2700      
                                                                 
 dense_1 (Dense)             (None, 25)                1525      
                                                                 
 dense_2 (Dense)             (None, 1)                 26        
                                                                 
Total params: 4,251
Trainable params: 4,251
Non-trainable params: 0
_________________________________________________________________


In [15]:
# Import checkpoint dependencies
import os
from tensorflow.keras.callbacks import ModelCheckpoint

In [16]:
# Compile the model
nn.compile(loss="binary_crossentropy", optimizer="adam", metrics=["accuracy"])

In [17]:
# Train the model   ***, callbacks=[cp_callback]***
fit_model = nn.fit(X_train_scaled, y_train, epochs=100)

Epoch 1/100
804/804 [==============================] - 3s 2ms/step - loss: 0.5712 - accuracy: 0.7212
Epoch 2/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5547 - accuracy: 0.7309
Epoch 3/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5516 - accuracy: 0.7335
Epoch 4/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5491 - accuracy: 0.7327
Epoch 5/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5485 - accuracy: 0.7346
Epoch 6/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5477 - accuracy: 0.7331
Epoch 7/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5462 - accuracy: 0.7332
Epoch 8/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5457 - accuracy: 0.7358
Epoch 9/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5453 - accuracy: 0.7345
Epoch 10/100
804/804 [==============================] - 2s 3ms/step - loss: 0.5447 - accura

804/804 [==============================] - 2s 2ms/step - loss: 0.5352 - accuracy: 0.7416
Epoch 82/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5351 - accuracy: 0.7416
Epoch 83/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5352 - accuracy: 0.7418
Epoch 84/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5351 - accuracy: 0.7414
Epoch 85/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5347 - accuracy: 0.7411
Epoch 86/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5349 - accuracy: 0.7418
Epoch 87/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5344 - accuracy: 0.7413
Epoch 88/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5343 - accuracy: 0.7409
Epoch 89/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5344 - accuracy: 0.7412
Epoch 90/100
804/804 [==============================] - 2s 2ms/step - loss: 0.5347 - accuracy: 

In [18]:
# Evaluate the model using the test data
model_loss, model_accuracy = nn.evaluate(X_test_scaled,y_test,verbose=2)
print(f"Loss: {model_loss}, Accuracy: {model_accuracy}")

268/268 - 1s - loss: 0.5575 - accuracy: 0.7243 - 568ms/epoch - 2ms/step
Loss: 0.5575460195541382, Accuracy: 0.7243148684501648


In [19]:
#Setup to find best options
# Create a method that creates a new Sequential model with hyperparameter options
def create_model(hp):
    nn_model = tf.keras.models.Sequential()

    # Allow kerastuner to decide which activation function to use in hidden layers
    activation = hp.Choice('activation',['relu','tanh','sigmoid'])
    
    # Allow kerastuner to decide number of neurons in first layer
    nn_model.add(tf.keras.layers.Dense(units=hp.Int('first_units',
        min_value=1,
        max_value=100,
        step=2), activation=activation, input_dim=44))

    # Allow kerastuner to decide number of hidden layers and neurons in hidden layers
    for i in range(hp.Int('num_layers', 1, 6)):
        nn_model.add(tf.keras.layers.Dense(units=hp.Int('units_' + str(i),
            min_value=1,
            max_value=100,
            step=2),
            activation=activation))
    
    nn_model.add(tf.keras.layers.Dense(units=1, activation="sigmoid"))

    # Compile the model
    nn_model.compile(loss="binary_crossentropy", optimizer='adam', metrics=["accuracy"])
    
    return nn_model

In [20]:
# Import the kerastuner library
!pip install keras-tuner
import kerastuner as kt

tuner = kt.Hyperband(
    create_model,
    objective="val_accuracy",
    overwrite=True,
    max_epochs=20,
    hyperband_iterations=2)

     -------------------------------------- 172.2/172.2 kB 1.1 MB/s eta 0:00:00


C:\Users\ethan\anaconda3\envs\mlenv\lib\site-packages\ipykernel_launcher.py:3: DeprecationWarning: `import kerastuner` is deprecated, please use `import keras_tuner`.
  This is separate from the ipykernel package so we can avoid doing imports until


In [21]:
# Run the kerastuner search for best hyperparameters
tuner.search(X_train_scaled,y_train,epochs=20,validation_data=(X_test_scaled,y_test))

Trial 60 Complete [00h 00m 59s]
val_accuracy: 0.7268804907798767

Best val_accuracy So Far: 0.7273469567298889
Total elapsed time: 00h 22m 44s
INFO:tensorflow:Oracle triggered exit


In [22]:
# Get best model hyperparameters
best_hyper = tuner.get_best_hyperparameters(1)[0]
best_hyper.values

{'activation': 'tanh',
 'first_units': 23,
 'num_layers': 4,
 'units_0': 27,
 'units_1': 55,
 'units_2': 63,
 'units_3': 53,
 'units_4': 97,
 'units_5': 7,
 'tuner/epochs': 20,
 'tuner/initial_epoch': 0,
 'tuner/bracket': 0,
 'tuner/round': 0}

In [23]:
# Evaluate best model against full test data
best_model = tuner.get_best_models(1)[0]
model_loss, model_accuracy = best_model.evaluate(X_test_scaled,y_test,verbose=2)
print(f"Loss: {model_loss}, Accuracy: {model_accuracy}")

268/268 - 1s - loss: 0.5532 - accuracy: 0.7273 - 701ms/epoch - 3ms/step
Loss: 0.5532264113426208, Accuracy: 0.7273469567298889


In [24]:
#  Import and read the charity_data.csv for new testing #3
import pandas as pd 
application_df2 = pd.read_csv("charity_data.csv")
application_df2.head()

EIN                                      NAME APPLICATION_TYPE  \
0  10520599              BLUE KNIGHTS MOTORCYCLE CLUB              T10   
1  10531628    AMERICAN CHESAPEAKE CLUB CHARITABLE TR               T3   
2  10547893        ST CLOUD PROFESSIONAL FIREFIGHTERS               T5   
3  10553066            SOUTHSIDE ATHLETIC ASSOCIATION               T3   
4  10556103  GENETIC RESEARCH INSTITUTE OF THE DESERT               T3   

        AFFILIATION CLASSIFICATION      USE_CASE  ORGANIZATION  STATUS  \
0       Independent          C1000    ProductDev   Association       1   
1       Independent          C2000  Preservation  Co-operative       1   
2  CompanySponsored          C3000    ProductDev   Association       1   
3  CompanySponsored          C2000  Preservation         Trust       1   
4       Independent          C1000     Heathcare         Trust       1   

      INCOME_AMT SPECIAL_CONSIDERATIONS  ASK_AMT  IS_SUCCESSFUL  
0              0                      N     5000              1  
1         1-9999                      N   108590              1  
2              0                      N     5000              0  
3    10000-24999                      N     6692              1  
4  100000-499999                      N   142590              1

In [25]:
# Determine the number of unique values in each column.
application_cat2 = application_df2.dtypes[application_df2.dtypes == "object"].index.tolist()
application_df2[application_cat2].nunique()

NAME                      19568
APPLICATION_TYPE             17
AFFILIATION                   6
CLASSIFICATION               71
USE_CASE                      5
ORGANIZATION                  4
INCOME_AMT                    9
SPECIAL_CONSIDERATIONS        2
dtype: int64

In [26]:
# Look at NAME value counts for binning
names2 = application_df2.NAME.value_counts()
names2

PARENT BOOSTER USA INC                                                  1260
TOPS CLUB INC                                                            765
UNITED STATES BOWLING CONGRESS INC                                       700
WASHINGTON STATE UNIVERSITY                                              492
AMATEUR ATHLETIC UNION OF THE UNITED STATES INC                          408
                                                                        ... 
ST LOUIS SLAM WOMENS FOOTBALL                                              1
AIESEC ALUMNI IBEROAMERICA CORP                                            1
WEALLBLEEDRED ORG INC                                                      1
AMERICAN SOCIETY FOR STANDARDS IN MEDIUMSHIP & PSYCHICAL INVESTIGATI       1
WATERHOUSE CHARITABLE TR                                                   1
Name: NAME, Length: 19568, dtype: int64

In [27]:
# Determine which values to replace if counts are less than ...?
replace_name2 = list(names2[names2 < 2].index)
    
# Replace in dataframe
for name in replace_name2:
    application_df2.NAME = application_df2.NAME.replace(name,"Other")
    
# Check to make sure binning was successful
application_df2.NAME.value_counts()

Other                                                                 18776
PARENT BOOSTER USA INC                                                 1260
TOPS CLUB INC                                                           765
UNITED STATES BOWLING CONGRESS INC                                      700
WASHINGTON STATE UNIVERSITY                                             492
                                                                      ...  
WASHINGTON EXPLORER SEARCH AND RESCUE                                     2
INTERNATIONAL ALLIANCE THEATRICAL STAGE EMPLOYEES & MOVING PICTURE        2
BIRTH NETWORK                                                             2
NATIONAL ASSOCIATON OF CORPORATE DIRECTORS                                2
NATIONAL SOCIETY COLONIAL DAMES XVII CENTURY                              2
Name: NAME, Length: 793, dtype: int64

In [28]:
# Look at APPLICATION_TYPE value counts for binning
app_type2 = application_df2.APPLICATION_TYPE.value_counts()
app_type2

T3     27037
T4      1542
T6      1216
T5      1173
T19     1065
T8       737
T7       725
T10      528
T9       156
T13       66
T12       27
T2        16
T25        3
T14        3
T29        2
T15        2
T17        1
Name: APPLICATION_TYPE, dtype: int64

In [29]:
# Determine which values to replace if counts are less than ...?
replace_application2 = list(app_type2[app_type2 < 200].index)
    
# Replace in dataframe
for app in replace_application2:
    application_df2.APPLICATION_TYPE = application_df2.APPLICATION_TYPE.replace(app,"Other")
    
# Check to make sure binning was successful
application_df2.APPLICATION_TYPE.value_counts()

T3       27037
T4        1542
T6        1216
T5        1173
T19       1065
T8         737
T7         725
T10        528
Other      276
Name: APPLICATION_TYPE, dtype: int64

In [30]:
# Look at CLASSIFICATION value counts for binning
class_val2 = application_df2.CLASSIFICATION.value_counts()
class_val2.head()

C1000    17326
C2000     6074
C1200     4837
C3000     1918
C2100     1883
Name: CLASSIFICATION, dtype: int64

In [31]:
# Determine which values to replace if counts are less than ..?
replace_class2 = list(class_val2[class_val2 < 300].index)

# Replace in dataframe
for cls in replace_class2:
    application_df2.CLASSIFICATION = application_df2.CLASSIFICATION.replace(cls,"Other")
    
# Check to make sure binning was successful
application_df2.CLASSIFICATION.value_counts()

C1000    17326
C2000     6074
C1200     4837
C3000     1918
C2100     1883
Other     1484
C7000      777
Name: CLASSIFICATION, dtype: int64

In [32]:
application_df2[application_cat2].nunique()

NAME                      793
APPLICATION_TYPE            9
AFFILIATION                 6
CLASSIFICATION              7
USE_CASE                    5
ORGANIZATION                4
INCOME_AMT                  9
SPECIAL_CONSIDERATIONS      2
dtype: int64

In [33]:
# Create a OneHotEncoder instance
enc = OneHotEncoder(sparse=False)

# Fit and transform the OneHotEncoder using the categorical variable list
encode_df2 = pd.DataFrame(enc.fit_transform(application_df2[application_cat2]))

# Add the encoded variable names to the dataframe
encode_df2.columns = enc.get_feature_names_out(application_cat2)
encode_df2.head()

NAME_4-H CLUBS & AFFILIATED 4-H ORGANIZATIONS  NAME_AACE INTERNATIONAL  \
0                                            0.0                      0.0   
1                                            0.0                      0.0   
2                                            0.0                      0.0   
3                                            0.0                      0.0   
4                                            0.0                      0.0   

   NAME_ACADEMY OF GENERAL DENTISTRY  NAME_ACADEMY OF MANAGED CARE PHARMACY  \
0                                0.0                                    0.0   
1                                0.0                                    0.0   
2                                0.0                                    0.0   
3                                0.0                                    0.0   
4                                0.0                                    0.0   

   NAME_ACE MENTOR PROGRAM OF AMERICA INC  \
0                                     0.0   
1                                     0.0   
2                                     0.0   
3                                     0.0   
4                                     0.0   

   NAME_ACTIVE 20-30 UNITED STATES AND CANADA  NAME_ACTS MINISTRY  \
0                                         0.0                 0.0   
1                                         0.0                 0.0   
2                                         0.0                 0.0   
3                                         0.0                 0.0   
4                                         0.0                 0.0   

   NAME_ACTS MISSIONS  \
0                 0.0   
1                 0.0   
2                 0.0   
3                 0.0   
4                 0.0   

   NAME_AFRICAN-AMERICAN POSTAL LEAGUE UNITED FOR SUCCESS A-PLUS  \
0                                                0.0               
1                                                0.0               
2                                                0.0               
3                                                0.0               
4                                                0.0               

   NAME_AGENTS ASSOCIATION  ...  INCOME_AMT_1-9999  INCOME_AMT_10000-24999  \
0                      0.0  ...                0.0                     0.0   
1                      0.0  ...                1.0                     0.0   
2                      0.0  ...                0.0                     0.0   
3                      0.0  ...                0.0                     1.0   
4                      0.0  ...                0.0                     0.0   

   INCOME_AMT_100000-499999  INCOME_AMT_10M-50M  INCOME_AMT_1M-5M  \
0                       0.0                 0.0               0.0   
1                       0.0                 0.0               0.0   
2                       0.0                 0.0               0.0   
3                       0.0                 0.0               0.0   
4                       1.0                 0.0               0.0   

   INCOME_AMT_25000-99999  INCOME_AMT_50M+  INCOME_AMT_5M-10M  \
0                     0.0              0.0                0.0   
1                     0.0              0.0                0.0   
2                     0.0              0.0                0.0   
3                     0.0              0.0                0.0   
4                     0.0              0.0                0.0   

   SPECIAL_CONSIDERATIONS_N  SPECIAL_CONSIDERATIONS_Y  
0                       1.0                       0.0  
1                       1.0                       0.0  
2                       1.0                       0.0  
3                       1.0                       0.0  
4                       1.0                       0.0  

[5 rows x 835 columns]

In [34]:
# Merge one-hot encoded features and drop the originals
application_df2 = application_df2.merge(encode_df2,left_index=True, right_index=True)
application_df2 = application_df2.drop(application_cat2,1)
application_df2.head()

C:\Users\ethan\anaconda3\envs\mlenv\lib\site-packages\ipykernel_launcher.py:3: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  This is separate from the ipykernel package so we can avoid doing imports until


EIN  STATUS  ASK_AMT  IS_SUCCESSFUL  \
0  10520599       1     5000              1   
1  10531628       1   108590              1   
2  10547893       1     5000              0   
3  10553066       1     6692              1   
4  10556103       1   142590              1   

   NAME_4-H CLUBS & AFFILIATED 4-H ORGANIZATIONS  NAME_AACE INTERNATIONAL  \
0                                            0.0                      0.0   
1                                            0.0                      0.0   
2                                            0.0                      0.0   
3                                            0.0                      0.0   
4                                            0.0                      0.0   

   NAME_ACADEMY OF GENERAL DENTISTRY  NAME_ACADEMY OF MANAGED CARE PHARMACY  \
0                                0.0                                    0.0   
1                                0.0                                    0.0   
2                                0.0                                    0.0   
3                                0.0                                    0.0   
4                                0.0                                    0.0   

   NAME_ACE MENTOR PROGRAM OF AMERICA INC  \
0                                     0.0   
1                                     0.0   
2                                     0.0   
3                                     0.0   
4                                     0.0   

   NAME_ACTIVE 20-30 UNITED STATES AND CANADA  ...  INCOME_AMT_1-9999  \
0                                         0.0  ...                0.0   
1                                         0.0  ...                1.0   
2                                         0.0  ...                0.0   
3                                         0.0  ...                0.0   
4                                         0.0  ...                0.0   

   INCOME_AMT_10000-24999  INCOME_AMT_100000-499999  INCOME_AMT_10M-50M  \
0                     0.0                       0.0                 0.0   
1                     0.0                       0.0                 0.0   
2                     0.0                       0.0                 0.0   
3                     1.0                       0.0                 0.0   
4                     0.0                       1.0                 0.0   

   INCOME_AMT_1M-5M  INCOME_AMT_25000-99999  INCOME_AMT_50M+  \
0               0.0                     0.0              0.0   
1               0.0                     0.0              0.0   
2               0.0                     0.0              0.0   
3               0.0                     0.0              0.0   
4               0.0                     0.0              0.0   

   INCOME_AMT_5M-10M  SPECIAL_CONSIDERATIONS_N  SPECIAL_CONSIDERATIONS_Y  
0                0.0                       1.0                       0.0  
1                0.0                       1.0                       0.0  
2                0.0                       1.0                       0.0  
3                0.0                       1.0                       0.0  
4                0.0                       1.0                       0.0  

[5 rows x 839 columns]

In [35]:
# Split our preprocessed data into our features and target arrays
y2 = application_df2.IS_SUCCESSFUL.values
X2 = application_df2.drop(["IS_SUCCESSFUL"], 1).values

# Split the preprocessed data into a training and testing dataset
X_train2, X_test2, y_train2, y_test2 = train_test_split(X2, y2, random_state=42, stratify=y2)

C:\Users\ethan\anaconda3\envs\mlenv\lib\site-packages\ipykernel_launcher.py:3: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  This is separate from the ipykernel package so we can avoid doing imports until


In [36]:
# Create a StandardScaler instances
scaler2 = StandardScaler()

# Fit the StandardScaler
X_scaler2 = scaler2.fit(X_train2)

# Scale the data
X_train_scaled2 = X_scaler2.transform(X_train2)
X_test_scaled2 = X_scaler2.transform(X_test2)

In [37]:
#Setup to find best options
# Create a method that creates a new Sequential model with hyperparameter options
def create_model(hp2):
    nn_model2 = tf.keras.models.Sequential()
    number_input_features2 = len(X_train_scaled2[0])

    # Allow kerastuner to decide which activation function to use in hidden layers
    activation2 = hp2.Choice('activation',['relu','tanh','sigmoid'])
    
    # Allow kerastuner to decide number of neurons in first layer
    nn_model2.add(tf.keras.layers.Dense(units=hp2.Int('first_units',
        min_value=1,
        max_value=100,
        step=2), activation=activation2, input_dim=number_input_features2))

    # Allow kerastuner to decide number of hidden layers and neurons in hidden layers
    for i in range(hp2.Int('num_layers', 1, 10)):
        nn_model2.add(tf.keras.layers.Dense(units=hp2.Int('units_' + str(i),
            min_value=1,
            max_value=100,
            step=2),
            activation=activation2))
    
    nn_model2.add(tf.keras.layers.Dense(units=1, activation="sigmoid"))

    # Compile the model
    nn_model2.compile(loss="binary_crossentropy", optimizer='adam', metrics=["accuracy"])
    
    return nn_model2

In [38]:
#Tuner is the same as the last model
import kerastuner as kt

tuner = kt.Hyperband(
    create_model,
    objective="val_accuracy",
    overwrite=True,
    max_epochs=20,
    hyperband_iterations=2)

In [39]:
# Run the kerastuner search for best hyperparameters
tuner.search(X_train_scaled2,y_train2,epochs=20,validation_data=(X_test_scaled2,y_test2))

Trial 60 Complete [00h 01m 20s]
val_accuracy: 0.7996501326560974

Best val_accuracy So Far: 0.8009329438209534
Total elapsed time: 00h 31m 43s
INFO:tensorflow:Oracle triggered exit


In [40]:
# Get best model hyperparameters
best_hyper2 = tuner.get_best_hyperparameters(1)[0]
best_hyper2.values

{'activation': 'tanh',
 'first_units': 43,
 'num_layers': 4,
 'units_0': 43,
 'units_1': 61,
 'units_2': 45,
 'units_3': 57,
 'units_4': 15,
 'units_5': 5,
 'units_6': 53,
 'tuner/epochs': 20,
 'tuner/initial_epoch': 7,
 'tuner/bracket': 2,
 'tuner/round': 2,
 'tuner/trial_id': '0014'}

In [41]:
# Evaluate best model against full test data
best_model2 = tuner.get_best_models(1)[0]
model_loss2, model_accuracy2 = best_model2.evaluate(X_test_scaled2,y_test2,verbose=2)
print(f"Loss: {model_loss2}, Accuracy: {model_accuracy2}")

268/268 - 1s - loss: 0.4328 - accuracy: 0.8009 - 891ms/epoch - 3ms/step
Loss: 0.4327846169471741, Accuracy: 0.8009329438209534


In [42]:
#Possible best current solution
number_input_features3 = len(X_train_scaled2[0])
hidden_nodes_layer1 = 73
hidden_nodes_layer2 = 49

nn3 = tf.keras.models.Sequential()

# First hidden layer
nn3.add(
    tf.keras.layers.Dense(units=hidden_nodes_layer1, input_dim=number_input_features3, activation="tanh")
)

# Second hidden layer
nn3.add(tf.keras.layers.Dense(units=hidden_nodes_layer2, activation="tanh"))

# Output layer
nn3.add(tf.keras.layers.Dense(units=1, activation="sigmoid"))

# Check the structure of the model
nn3.summary()

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense_6 (Dense)             (None, 73)                61247     
                                                                 
 dense_7 (Dense)             (None, 49)                3626      
                                                                 
 dense_8 (Dense)             (None, 1)                 50        
                                                                 
Total params: 64,923
Trainable params: 64,923
Non-trainable params: 0
_________________________________________________________________


In [43]:
# Import checkpoint dependencies
import os
from tensorflow.keras.callbacks import ModelCheckpoint

# Define the checkpoint path and filenames
os.makedirs("checkpoints/",exist_ok=True)
checkpoint_path = "checkpoints/weights.{epoch:02d}.hdf5"

In [44]:
# Compile the model
nn3.compile(loss="binary_crossentropy", optimizer="adam", metrics=["accuracy"])

# Create a callback that saves the model's weights every 5 epoch
cp_callback = ModelCheckpoint(
    filepath=checkpoint_path,
    verbose=1,
    save_weights_only=True,
    save_freq= 5)

In [45]:
#Train the model 
fit_model3 = nn3.fit(X_train_scaled2, y_train2, epochs=200, callbacks=[cp_callback])

Epoch 1/200
  1/804 [..............................] - ETA: 13:17 - loss: 0.6820 - accuracy: 0.5625
Epoch 1: saving model to checkpoints\weights.01.hdf5
  5/804 [..............................] - ETA: 12s - loss: 0.6672 - accuracy: 0.6062  
Epoch 1: saving model to checkpoints\weights.01.hdf5
 14/804 [..............................] - ETA: 6s - loss: 0.6413 - accuracy: 0.6451 
Epoch 1: saving model to checkpoints\weights.01.hdf5

Epoch 1: saving model to checkpoints\weights.01.hdf5
 20/804 [..............................] - ETA: 7s - loss: 0.6307 - accuracy: 0.6562
Epoch 1: saving model to checkpoints\weights.01.hdf5
 29/804 [>.............................] - ETA: 6s - loss: 0.6083 - accuracy: 0.6843
Epoch 1: saving model to checkpoints\weights.01.hdf5

Epoch 1: saving model to checkpoints\weights.01.hdf5
 35/804 [>.............................] - ETA: 6s - loss: 0.6036 - accuracy: 0.6911
Epoch 1: saving model to checkpoints\weights.01.hdf5
 41/804 [>.............................] - ET

365/804 [============>.................] - ETA: 3s - loss: 0.4855 - accuracy: 0.7676
Epoch 1: saving model to checkpoints\weights.01.hdf5

Epoch 1: saving model to checkpoints\weights.01.hdf5
375/804 [============>.................] - ETA: 3s - loss: 0.4846 - accuracy: 0.7680
Epoch 1: saving model to checkpoints\weights.01.hdf5

Epoch 1: saving model to checkpoints\weights.01.hdf5
385/804 [=============>................] - ETA: 3s - loss: 0.4825 - accuracy: 0.7696
Epoch 1: saving model to checkpoints\weights.01.hdf5
394/804 [=============>................] - ETA: 3s - loss: 0.4815 - accuracy: 0.7702
Epoch 1: saving model to checkpoints\weights.01.hdf5

Epoch 1: saving model to checkpoints\weights.01.hdf5
400/804 [=============>................] - ETA: 3s - loss: 0.4798 - accuracy: 0.7709
Epoch 1: saving model to checkpoints\weights.01.hdf5
408/804 [==============>...............] - ETA: 3s - loss: 0.4791 - accuracy: 0.7709
Epoch 1: saving model to checkpoints\weights.01.hdf5

Epoch 1: 

754/804 [===========================>..] - ETA: 0s - loss: 0.4605 - accuracy: 0.7811
Epoch 1: saving model to checkpoints\weights.01.hdf5

Epoch 1: saving model to checkpoints\weights.01.hdf5
760/804 [===========================>..] - ETA: 0s - loss: 0.4600 - accuracy: 0.7815
Epoch 1: saving model to checkpoints\weights.01.hdf5
768/804 [===========================>..] - ETA: 0s - loss: 0.4596 - accuracy: 0.7817
Epoch 1: saving model to checkpoints\weights.01.hdf5

Epoch 1: saving model to checkpoints\weights.01.hdf5
775/804 [===========================>..] - ETA: 0s - loss: 0.4596 - accuracy: 0.7818
Epoch 1: saving model to checkpoints\weights.01.hdf5
780/804 [============================>.] - ETA: 0s - loss: 0.4594 - accuracy: 0.7818
Epoch 1: saving model to checkpoints\weights.01.hdf5
786/804 [============================>.] - ETA: 0s - loss: 0.4594 - accuracy: 0.7818
Epoch 1: saving model to checkpoints\weights.01.hdf5
791/804 [============================>.] - ETA: 0s - loss: 0.459

320/804 [==========>...................] - ETA: 3s - loss: 0.4180 - accuracy: 0.8014
Epoch 2: saving model to checkpoints\weights.02.hdf5

Epoch 2: saving model to checkpoints\weights.02.hdf5
326/804 [===========>..................] - ETA: 3s - loss: 0.4186 - accuracy: 0.8007
Epoch 2: saving model to checkpoints\weights.02.hdf5
335/804 [===========>..................] - ETA: 3s - loss: 0.4176 - accuracy: 0.8011
Epoch 2: saving model to checkpoints\weights.02.hdf5

Epoch 2: saving model to checkpoints\weights.02.hdf5
341/804 [===========>..................] - ETA: 3s - loss: 0.4177 - accuracy: 0.8010
Epoch 2: saving model to checkpoints\weights.02.hdf5
349/804 [============>.................] - ETA: 3s - loss: 0.4173 - accuracy: 0.8015
Epoch 2: saving model to checkpoints\weights.02.hdf5

Epoch 2: saving model to checkpoints\weights.02.hdf5
356/804 [============>.................] - ETA: 3s - loss: 0.4186 - accuracy: 0.8007
Epoch 2: saving model to checkpoints\weights.02.hdf5

Epoch 2: 


Epoch 2: saving model to checkpoints\weights.02.hdf5
686/804 [========================>.....] - ETA: 0s - loss: 0.4156 - accuracy: 0.8051
Epoch 2: saving model to checkpoints\weights.02.hdf5

Epoch 2: saving model to checkpoints\weights.02.hdf5
696/804 [========================>.....] - ETA: 0s - loss: 0.4155 - accuracy: 0.8054
Epoch 2: saving model to checkpoints\weights.02.hdf5
704/804 [=========================>....] - ETA: 0s - loss: 0.4159 - accuracy: 0.8050
Epoch 2: saving model to checkpoints\weights.02.hdf5

Epoch 2: saving model to checkpoints\weights.02.hdf5
711/804 [=========================>....] - ETA: 0s - loss: 0.4156 - accuracy: 0.8052
Epoch 2: saving model to checkpoints\weights.02.hdf5
720/804 [=========================>....] - ETA: 0s - loss: 0.4154 - accuracy: 0.8056
Epoch 2: saving model to checkpoints\weights.02.hdf5

Epoch 2: saving model to checkpoints\weights.02.hdf5
726/804 [==========================>...] - ETA: 0s - loss: 0.4154 - accuracy: 0.8056
Epoch 2: 

...

288/804 [=========>....................] - ETA: 5s - loss: 0.3383 - accuracy: 0.8411
Epoch 199: saving model to checkpoints\weights.199.hdf5
293/804 [=========>....................] - ETA: 5s - loss: 0.3374 - accuracy: 0.8419
Epoch 199: saving model to checkpoints\weights.199.hdf5
298/804 [==========>...................] - ETA: 5s - loss: 0.3380 - accuracy: 0.8408
Epoch 199: saving model to checkpoints\weights.199.hdf5
303/804 [==========>...................] - ETA: 5s - loss: 0.3377 - accuracy: 0.8408
Epoch 199: saving model to checkpoints\weights.199.hdf5
308/804 [==========>...................] - ETA: 5s - loss: 0.3385 - accuracy: 0.8399
Epoch 199: saving model to checkpoints\weights.199.hdf5
313/804 [==========>...................] - ETA: 5s - loss: 0.3384 - accuracy: 0.8403
Epoch 199: saving model to checkpoints\weights.199.hdf5
319/804 [==========>...................] - ETA: 5s - loss: 0.3392 - accuracy: 0.8394
Epoch 199: saving model to checkpoints\weights.199.hdf5
324/804 [====

587/804 [====================>.........] - ETA: 2s - loss: 0.3400 - accuracy: 0.8403
Epoch 199: saving model to checkpoints\weights.199.hdf5
592/804 [=====================>........] - ETA: 2s - loss: 0.3400 - accuracy: 0.8401
Epoch 199: saving model to checkpoints\weights.199.hdf5

Epoch 199: saving model to checkpoints\weights.199.hdf5
598/804 [=====================>........] - ETA: 2s - loss: 0.3400 - accuracy: 0.8401
Epoch 199: saving model to checkpoints\weights.199.hdf5
604/804 [=====================>........] - ETA: 2s - loss: 0.3397 - accuracy: 0.8404
Epoch 199: saving model to checkpoints\weights.199.hdf5
610/804 [=====================>........] - ETA: 2s - loss: 0.3403 - accuracy: 0.8400
Epoch 199: saving model to checkpoints\weights.199.hdf5
615/804 [=====================>........] - ETA: 1s - loss: 0.3402 - accuracy: 0.8400
Epoch 199: saving model to checkpoints\weights.199.hdf5
621/804 [======================>.......] - ETA: 1s - loss: 0.3396 - accuracy: 0.8405
Epoch 199: s

 73/804 [=>............................] - ETA: 7s - loss: 0.3474 - accuracy: 0.8305
Epoch 200: saving model to checkpoints\weights.200.hdf5
 77/804 [=>............................] - ETA: 7s - loss: 0.3450 - accuracy: 0.8316
Epoch 200: saving model to checkpoints\weights.200.hdf5
 82/804 [==>...........................] - ETA: 7s - loss: 0.3447 - accuracy: 0.8319
Epoch 200: saving model to checkpoints\weights.200.hdf5
 86/804 [==>...........................] - ETA: 7s - loss: 0.3460 - accuracy: 0.8318
Epoch 200: saving model to checkpoints\weights.200.hdf5
 91/804 [==>...........................] - ETA: 7s - loss: 0.3424 - accuracy: 0.8345
Epoch 200: saving model to checkpoints\weights.200.hdf5
 96/804 [==>...........................] - ETA: 7s - loss: 0.3405 - accuracy: 0.8359
Epoch 200: saving model to checkpoints\weights.200.hdf5
100/804 [==>...........................] - ETA: 7s - loss: 0.3377 - accuracy: 0.8381
Epoch 200: saving model to checkpoints\weights.200.hdf5
104/804 [==>.

367/804 [============>.................] - ETA: 4s - loss: 0.3331 - accuracy: 0.8428
Epoch 200: saving model to checkpoints\weights.200.hdf5
373/804 [============>.................] - ETA: 4s - loss: 0.3327 - accuracy: 0.8430
Epoch 200: saving model to checkpoints\weights.200.hdf5
378/804 [=============>................] - ETA: 4s - loss: 0.3327 - accuracy: 0.8433
Epoch 200: saving model to checkpoints\weights.200.hdf5

Epoch 200: saving model to checkpoints\weights.200.hdf5
384/804 [=============>................] - ETA: 4s - loss: 0.3328 - accuracy: 0.8435
Epoch 200: saving model to checkpoints\weights.200.hdf5
390/804 [=============>................] - ETA: 4s - loss: 0.3326 - accuracy: 0.8437
Epoch 200: saving model to checkpoints\weights.200.hdf5
395/804 [=============>................] - ETA: 4s - loss: 0.3332 - accuracy: 0.8434
Epoch 200: saving model to checkpoints\weights.200.hdf5
401/804 [=============>................] - ETA: 4s - loss: 0.3336 - accuracy: 0.8434
Epoch 200: s

666/804 [=======================>......] - ETA: 1s - loss: 0.3373 - accuracy: 0.8415
Epoch 200: saving model to checkpoints\weights.200.hdf5
671/804 [========================>.....] - ETA: 1s - loss: 0.3373 - accuracy: 0.8414
Epoch 200: saving model to checkpoints\weights.200.hdf5
675/804 [========================>.....] - ETA: 1s - loss: 0.3378 - accuracy: 0.8413
Epoch 200: saving model to checkpoints\weights.200.hdf5
680/804 [========================>.....] - ETA: 1s - loss: 0.3380 - accuracy: 0.8412
Epoch 200: saving model to checkpoints\weights.200.hdf5
685/804 [========================>.....] - ETA: 1s - loss: 0.3381 - accuracy: 0.8410
Epoch 200: saving model to checkpoints\weights.200.hdf5
690/804 [========================>.....] - ETA: 1s - loss: 0.3384 - accuracy: 0.8410
Epoch 200: saving model to checkpoints\weights.200.hdf5
694/804 [========================>.....] - ETA: 1s - loss: 0.3381 - accuracy: 0.8413
Epoch 200: saving model to checkpoints\weights.200.hdf5
699/804 [====

In [46]:
# Evaluate the model using the test data
model_loss3, model_accuracy3 = nn3.evaluate(X_test_scaled2,y_test2,verbose=2)
print(f"Loss: {model_loss3}, Accuracy: {model_accuracy3}")

268/268 - 1s - loss: 0.5002 - accuracy: 0.7889 - 1s/epoch - 4ms/step
Loss: 0.5002471804618835, Accuracy: 0.7889212965965271


In [47]:
# Export our model to HDF5 file
nn3.save("AlphabetSoupCharity_Optimization.h5")